# Federated Learning (FL) Experiment Notebook (Annotated)

This notebook:
- Loads Borg trace data (uploaded as a ZIP)
- Cleans and flattens JSON-like columns into numeric features
- Splits data into multiple “nodes” (clients)
- Trains a simple FL model with FedAvg
- Tracks energy/CO₂ with CodeCarbon
- Runs experiments (4 / 8 / 12 nodes, different rounds) and saves results

> Tip: Run cells from top to bottom. If you're not using Google Colab, replace `/content/...` paths with local paths.


## 1) Upload and extract raw data
Upload the ZIP containing `borg_traces_data.csv`, then unzip it into `/content/trace_raw`.

In [1]:
# Upload ZIP file(s) containing the raw dataset.

from google.colab import files
uploaded = files.upload()


Saving borg_traces_data.csv.zip to borg_traces_data.csv.zip


In [2]:
# Unzip uploaded data into a working folder.

!unzip *.zip -d /content/trace_raw


Archive:  borg_traces_data.csv.zip
  inflating: /content/trace_raw/borg_traces_data.csv  


In [3]:
# Basic filesystem utilities.

import os
os.listdir('/content')


['.config',
 'borg_traces_data.csv.zip',
 '.ipynb_checkpoints',
 'trace_raw',
 'sample_data']

In [4]:
# Confirm unzipped contents.

os.listdir("/content/trace_raw")


['borg_traces_data.csv']

## 2) Quick sanity-check of the raw dataset
Load a small sample to confirm the file is readable and inspect columns.

In [5]:
# Load a small sample of the CSV to preview.

import pandas as pd

df = pd.read_csv("/content/trace_raw/borg_traces_data.csv", nrows=5)
df.head()


Unnamed: 0           time  instance_events_type  collection_id  \
0           0              0                     2    94591244395   
1           1  2517305308183                     2   260697606809   
2           2   195684022913                     6   276227177776   
3           3              0                     2    10507389885   
4           4  1810627494172                     3    25911621841   

   scheduling_class  collection_type  priority  alloc_collection_id  \
0                 3                1       200                    0   
1                 2                0       360         221495397286   
2                 2                0       103                    0   
3                 3                0       200                    0   
4                 2                0         0                    0   

   instance_index    machine_id  ... assigned_memory page_cache_memory  \
0             144  168846390496  ...        0.014435          0.000415   
1             335      85515092  ...        0.000000          0.000000   
2             376  169321752432  ...        0.010422          0.000235   
3            1977  178294817221  ...        0.041626          0.000225   
4            3907  231364893292  ...        0.000272          0.000010   

   cycles_per_instruction memory_accesses_per_instruction sample_rate  \
0                     NaN                             NaN         1.0   
1                     NaN                             NaN         1.0   
2                0.939919                        0.001318         1.0   
3                1.359102                        0.007643         1.0   
4                     NaN                             NaN         1.0   

                              cpu_usage_distribution  \
0  [0.00314331 0.00381088 0.00401306 0.00415039 0...   
1  [1.23977661e-05 1.23977661e-05 1.23977661e-05 ...   
2  [0.01344299 0.01809692 0.0201416  0.02246094 0...   
3  [0.03704834 0.04125977 0.04290771 0.04425049 0...   
4  [0.         0.         0.         0.         0...   

                         tail_cpu_usage_distribution  cluster     event  \
0  [0.00535583 0.00541687 0.00548553 0.00554657 0...        7      FAIL   
1  [1.23977661e-05 1.23977661e-05 1.23977661e-05 ...        7      FAIL   
2  [0.02902222 0.02929688 0.0295105  0.0296936  0...        7  SCHEDULE   
3  [0.05535889 0.05584717 0.05633545 0.05718994 0...        8      FAIL   
4  [0.00041485 0.00041485 0.00041485 0.00041485 0...        2    FINISH   

   failed  
0       1  
1       1  
2       0  
3       1  
4       0  

[5 rows x 34 columns]

In [6]:
# List column names (helps decide what to keep).

df.columns.tolist()


['Unnamed: 0',
 'time',
 'instance_events_type',
 'collection_id',
 'scheduling_class',
 'collection_type',
 'priority',
 'alloc_collection_id',
 'instance_index',
 'machine_id',
 'resource_request',
 'constraint',
 'collections_events_type',
 'user',
 'collection_name',
 'collection_logical_name',
 'start_after_collection_ids',
 'vertical_scaling',
 'scheduler',
 'start_time',
 'end_time',
 'average_usage',
 'maximum_usage',
 'random_sample_usage',
 'assigned_memory',
 'page_cache_memory',
 'cycles_per_instruction',
 'memory_accesses_per_instruction',
 'sample_rate',
 'cpu_usage_distribution',
 'tail_cpu_usage_distribution',
 'cluster',
 'event',
 'failed']

## 3) Data cleaning + feature engineering
Keep the columns we need, parse JSON-like fields, and produce a clean flat table saved as `clean_trace.csv`.

In [7]:
# Main cleaning step: select columns, parse JSON-like fields, and write `clean_trace.csv`.

import pandas as pd
import numpy as np
import json
from tqdm import tqdm

RAW_FILE = "/content/trace_raw/borg_traces_data.csv"

# Columns we WANT to keep
USE_COLS = [
    "time",
    "machine_id",
    "scheduling_class",
    "priority",
    "resource_request",
    "average_usage",
    "maximum_usage",
    "assigned_memory",
    "page_cache_memory",
    "cycles_per_instruction",
    "memory_accesses_per_instruction",
    "cpu_usage_distribution",
    "tail_cpu_usage_distribution",
    "cluster",
]

# Read CSV in chunks to avoid RAM crash
chunksize = 50000
clean_chunks = []

def safe_json_load(x):
    try:
        return json.loads(x.replace("'", '"')) if isinstance(x, str) else x
    except:
        return None

def parse_and_extract(value, key=None, transform_func=None):
    parsed_data = safe_json_load(value)
    if key: # Expecting a dictionary
        if isinstance(parsed_data, dict):
            return parsed_data.get(key, np.nan)
        return np.nan
    elif transform_func: # Expecting a list
        if isinstance(parsed_data, list):
            return transform_func(parsed_data)
        return np.nan
    return parsed_data # If no key or transform_func, just return the parsed data

for chunk in tqdm(pd.read_csv(RAW_FILE, chunksize=chunksize)):
    # Keep only useful columns
    chunk = chunk[USE_COLS].copy()
    # Convert microsecond Unix to datetime
    chunk["time"] = pd.to_datetime(chunk["time"], unit="us", errors="coerce")

    # FLATTEN JSON FIELDS(Reduce Dimensions)

    # resource_request flatten
    chunk["req_cpu"] = chunk["resource_request"].apply(lambda x: parse_and_extract(x, key="cpus"))
    chunk["req_mem"] = chunk["resource_request"].apply(lambda x: parse_and_extract(x, key="memory"))

    # average_usage flatten
    chunk["cpu_avg"] = chunk["average_usage"].apply(lambda x: parse_and_extract(x, key="cpus"))
    chunk["mem_avg"] = chunk["average_usage"].apply(lambda x: parse_and_extract(x, key="memory"))

    # maximum_usage flatten
    chunk["cpu_max"] = chunk["maximum_usage"].apply(lambda x: parse_and_extract(x, key="cpus"))
    chunk["mem_max"] = chunk["maximum_usage"].apply(lambda x: parse_and_extract(x, key="memory"))

    # histogram flatten (optional: only take mean)
    chunk["cpu_hist_mean"] = chunk["cpu_usage_distribution"].apply(
        lambda x: parse_and_extract(x, transform_func=np.mean)
    )
    chunk["cpu_tail_mean"] = chunk["tail_cpu_usage_distribution"].apply(
        lambda x: parse_and_extract(x, transform_func=np.mean)
    )

    # Add to list
    clean_chunks.append(chunk)

# Combine into one clean dataframe
df_clean = pd.concat(clean_chunks, ignore_index=True)

# Save the cleaned file
df_clean.to_csv("/content/clean_trace.csv", index=False)

df_clean.head(), df_clean.shape

0it [00:00, ?it/s]/usr/local/lib/python3.12/dist-packages/numpy/_core/fromnumeric.py:3596: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/usr/local/lib/python3.12/dist-packages/numpy/_core/_methods.py:138: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
/usr/local/lib/python3.12/dist-packages/numpy/_core/fromnumeric.py:3596: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/usr/local/lib/python3.12/dist-packages/numpy/_core/_methods.py:138: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
1it [00:02,  2.26s/it]/usr/local/lib/python3.12/dist-packages/numpy/_core/fromnumeric.py:3596: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/usr/local/lib/python3.12/dist-packages/numpy/_core/_methods.py:138: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.t

(                        time    machine_id  scheduling_class  priority  \
 0 1970-01-01 00:00:00.000000  168846390496                 3       200   
 1 1970-01-30 03:15:05.308183      85515092                 2       360   
 2 1970-01-03 06:21:24.022913  169321752432                 2       103   
 3 1970-01-01 00:00:00.000000  178294817221                 3       200   
 4 1970-01-21 22:57:07.494172  231364893292                 2         0   
 
                                     resource_request  \
 0  {'cpus': 0.020660400390625, 'memory': 0.014434...   
 1  {'cpus': 0.00724029541015625, 'memory': 0.0013...   
 2  {'cpus': 0.048583984375, 'memory': 0.004165649...   
 3  {'cpus': 0.0704345703125, 'memory': 0.04162597...   
 4  {'cpus': 0.00244903564453125, 'memory': 0.0002...   
 
                                        average_usage  \
 0  {'cpus': 0.00466156005859375, 'memory': 0.0059...   
 1       {'cpus': 0.0, 'memory': 9.5367431640625e-07}   
 2  {'cpus': 0.024200439453125, '

In [8]:
import pandas as pd
import numpy as np
import os

CLEAN_FILE = "/content/clean_trace.csv"
df = pd.read_csv(CLEAN_FILE)

print("Loaded clean dataset:", df.shape)

#Get the unique machine IDs
machines = sorted(df["machine_id"].unique().tolist())
num_machines = len(machines)

print("Total unique machines:", num_machines)

#Split into nodes(For FL)
num_nodes = 4
machines_split = np.array_split(machines, num_nodes)

node_paths = []

os.makedirs("/content/nodes", exist_ok=True)

for i, machine_group in enumerate(machines_split, start=1):
    node_df = df[df["machine_id"].isin(machine_group)].copy()

    node_path = f"/content/nodes/node_{i}.csv"
    node_df.to_csv(node_path, index=False)
    node_paths.append(node_path)

    print(f"Node {i}: {len(machine_group)} machines → {node_df.shape[0]} rows")

node_paths


Loaded clean dataset: (405894, 22)
Total unique machines: 96174
Node 1: 24044 machines → 95719 rows
Node 2: 24044 machines → 104015 rows
Node 3: 24043 machines → 104316 rows
Node 4: 24043 machines → 101844 rows


['/content/nodes/node_1.csv',
 '/content/nodes/node_2.csv',
 '/content/nodes/node_3.csv',
 '/content/nodes/node_4.csv']

In [9]:
import pandas as pd
import numpy as np
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error, mean_absolute_error
from sklearn.model_selection import train_test_split

#Load Node 1
node_path = "/content/nodes/node_1.csv"
df = pd.read_csv(node_path)

print("Node 1 loaded:", df.shape)

#  Basic cleaning
# Keep only rows with usable CPU usage
df = df.dropna(subset=["cpu_avg", "cpu_max"])

# Sort by time
df["time"] = pd.to_datetime(df["time"])
df = df.sort_values("time")

#Select features for prediction
FEATURES = [
    "cpu_avg", "cpu_max",
    "req_cpu", "req_mem",
    "mem_avg", "mem_max",
    "assigned_memory",
    "page_cache_memory",
    "cycles_per_instruction",
    "memory_accesses_per_instruction",
    "cpu_hist_mean",
    "cpu_tail_mean",
]

TARGET = "cpu_avg"     # Predict next-step CPU usage (energy signal)

# Impute NaNs in cpu_hist_mean and cpu_tail_mean with 0 before dropping other NaNs
# This is important because these columns might have many NaNs from empty distribution lists
df['cpu_hist_mean'] = df['cpu_hist_mean'].fillna(0)
df['cpu_tail_mean'] = df['cpu_tail_mean'].fillna(0)


# Drop rows missing any remaining feature
df = df.dropna(subset=FEATURES)

X = df[FEATURES].values
y = df[TARGET].shift(-1).values   # next-step prediction
df = df.iloc[:-1]                 # drop last row without target

X = X[:-1]
y = y[:-1]

#Tt Split
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, shuffle=False
)

#Train Random Forest
model = RandomForestRegressor(
    n_estimators=150,
    max_depth=12,
    random_state=42,
    n_jobs=-1
)

model.fit(X_train, y_train)

#Evaluate
preds = model.predict(X_test)

rmse = np.sqrt(mean_squared_error(y_test, preds))
mae = mean_absolute_error(y_test, preds)
#mape = np.mean(np.abs((y_test - preds) / (y_test + 1e-6))) * 100
#Compute SMAPE (Using SMAPE and not MAPE because our Target varaible which ia CPU_Avg has many values that is closer to zero and when this happens it explodes so we get high figures )
def smape(y_true, y_pred):
    denominator = (np.abs(y_true) + np.abs(y_pred)) / 2
    diff = np.abs(y_true - y_pred) / (denominator + 1e-6)
    return np.mean(diff) * 100

smape_val = smape(y_test, preds)

print("\n=== BASELINE LOCAL MODEL — NODE 1 ===")
print(f"RMSE: {rmse:.6f}")
print(f"MAE : {mae:.6f}")
print(f"SMAPE: {smape_val:.2f}%")


#Save model output
import joblib
joblib.dump(model, "/content/node1_baseline_model.pkl")

print("\nSaved Node 1 model → node1_baseline_model.pkl")

Node 1 loaded: (95719, 22)

=== BASELINE LOCAL MODEL — NODE 1 ===
RMSE: 0.008886
MAE : 0.005196
SMAPE: 116.21%

Saved Node 1 model → node1_baseline_model.pkl


## 4) Install and set up energy / CO₂ tracking
We use **CodeCarbon** to track energy consumption and estimated CO₂ emissions.

In [10]:
# Install CodeCarbon for energy/CO₂ tracking.

!pip install codecarbon


In [11]:
from codecarbon import EmissionsTracker
import joblib
import glob
import numpy as np
import pandas as pd
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, mean_absolute_error

def smape(y_true, y_pred):
    denominator = (np.abs(y_true) + np.abs(y_pred)) / 2
    diff = np.abs(y_true - y_pred) / (denominator + 1e-6)
    return np.mean(diff) * 100

node_files = sorted(glob.glob("/content/nodes/node_*.csv"))

results = []

for path in node_files:
    print("\n====================")
    print("Training baseline for:", path)

    # Start energy tracker
    tracker = EmissionsTracker(project_name=f"{path}_baseline", measure_power_secs=1)
    tracker.start()

    df = pd.read_csv(path)

    # Clean dataset
    df = df.dropna(subset=["cpu_avg", "cpu_max"])
    df["time"] = pd.to_datetime(df["time"])
    df = df.sort_values("time")

    FEATURES = [
        "cpu_avg", "cpu_max",
        "req_cpu", "req_mem",
        "mem_avg", "mem_max",
        "assigned_memory",
        "page_cache_memory",
        "cycles_per_instruction",
        "memory_accesses_per_instruction",
        "cpu_hist_mean",
        "cpu_tail_mean",
    ]

    TARGET = "cpu_avg"

    # Fix NaNs in distribution means
    df['cpu_hist_mean'] = df['cpu_hist_mean'].fillna(0)
    df['cpu_tail_mean'] = df['cpu_tail_mean'].fillna(0)

    df = df.dropna(subset=FEATURES)

    if df.empty:
        print(f"Warning: Empty dataset for {path}. Skipping.")
        tracker.stop()
        continue

    X = df[FEATURES].values
    y = df[TARGET].shift(-1).values

    df = df.iloc[:-1]
    X = X[:-1]
    y = y[:-1]

    if len(X) == 0 or len(y) == 0:
        print(f"Warning: No usable rows for {path}. Skipping.")
        tracker.stop()
        continue

    X_train, X_test, y_train, y_test = train_test_split(
        X, y, test_size=0.2, shuffle=False
    )

    # Train baseline model
    model = RandomForestRegressor(
        n_estimators=150,
        max_depth=12,
        random_state=42,
        n_jobs=-1
    )
    model.fit(X_train, y_train)
    preds = model.predict(X_test)

    # Stop energy tracker and capture CO₂ + energy data
    co2_kg = tracker.stop()

    # Extract detailed energy numbers from final_emissions_data
    final_data = tracker.final_emissions_data
    total_energy_kwh = final_data.energy_consumed if final_data else 0
    cpu_energy_kwh = final_data.cpu_energy if final_data else 0
    ram_energy_kwh = final_data.ram_energy if final_data else 0

    # Metrics
    rmse = np.sqrt(mean_squared_error(y_test, preds))
    mae = mean_absolute_error(y_test, preds)
    smape_val = smape(y_test, preds)

    results.append({
        "node": path,
        "rmse": rmse,
        "mae": mae,
        "smape": smape_val,
        "co2_kg": co2_kg,
        "energy_kwh": total_energy_kwh,
        "cpu_energy_kwh": cpu_energy_kwh,
        "ram_energy_kwh": ram_energy_kwh
    })

    # Save model
    model_name = path.replace(".csv", "_baseline.pkl")
    joblib.dump(model, model_name)
    print(f"Saved model to {model_name}")

# Final results as DataFrame
results_df = pd.DataFrame(results)
print("\n=== BASELINE ENERGY + METRICS FOR ALL NODES ===")
print(results_df)

[codecarbon WARNING @ 00:57:30] Multiple instances of codecarbon are allowed to run at the same time.
[codecarbon INFO @ 00:57:30] [setup] RAM Tracking...
[codecarbon INFO @ 00:57:30] [setup] CPU Tracking...



Training baseline for: /content/nodes/node_1.csv


[codecarbon WARNING @ 00:57:31] We saw that you have a Intel(R) Xeon(R) CPU @ 2.20GHz but we don't know it. Please contact us.
[codecarbon WARNING @ 00:57:31] No CPU tracking mode found. Falling back on estimation based on TDP for CPU. 
 Linux OS detected: Please ensure RAPL files exist, and are readable, at /sys/class/powercap/intel-rapl/subsystem to measure CPU

[codecarbon INFO @ 00:57:31] CPU Model on constant consumption mode: Intel(R) Xeon(R) CPU @ 2.20GHz
[codecarbon WARNING @ 00:57:31] No CPU tracking mode found. Falling back on CPU constant mode.
[codecarbon INFO @ 00:57:31] [setup] GPU Tracking...
[codecarbon INFO @ 00:57:31] No GPU found.
[codecarbon INFO @ 00:57:31] The below tracking methods have been set up:
                RAM Tracking Method: RAM power estimation model
                CPU Tracking Method: global constant
                GPU Tracking Method: Unspecified
            
[codecarbon INFO @ 00:57:31] >>> Tracker's metadata:
[codecarbon INFO @ 00:57:31]   Platf

Saved model to /content/nodes/node_1_baseline.pkl

Training baseline for: /content/nodes/node_2.csv


[codecarbon WARNING @ 00:58:09] We saw that you have a Intel(R) Xeon(R) CPU @ 2.20GHz but we don't know it. Please contact us.
[codecarbon WARNING @ 00:58:09] No CPU tracking mode found. Falling back on estimation based on TDP for CPU. 
 Linux OS detected: Please ensure RAPL files exist, and are readable, at /sys/class/powercap/intel-rapl/subsystem to measure CPU

[codecarbon INFO @ 00:58:09] CPU Model on constant consumption mode: Intel(R) Xeon(R) CPU @ 2.20GHz
[codecarbon WARNING @ 00:58:09] No CPU tracking mode found. Falling back on CPU constant mode.
[codecarbon INFO @ 00:58:09] [setup] GPU Tracking...
[codecarbon INFO @ 00:58:09] No GPU found.
[codecarbon INFO @ 00:58:09] The below tracking methods have been set up:
                RAM Tracking Method: RAM power estimation model
                CPU Tracking Method: global constant
                GPU Tracking Method: Unspecified
            
[codecarbon INFO @ 00:58:09] >>> Tracker's metadata:
[codecarbon INFO @ 00:58:09]   Platf

Saved model to /content/nodes/node_2_baseline.pkl

Training baseline for: /content/nodes/node_3.csv


[codecarbon WARNING @ 00:58:32] We saw that you have a Intel(R) Xeon(R) CPU @ 2.20GHz but we don't know it. Please contact us.
[codecarbon WARNING @ 00:58:32] No CPU tracking mode found. Falling back on estimation based on TDP for CPU. 
 Linux OS detected: Please ensure RAPL files exist, and are readable, at /sys/class/powercap/intel-rapl/subsystem to measure CPU

[codecarbon INFO @ 00:58:32] CPU Model on constant consumption mode: Intel(R) Xeon(R) CPU @ 2.20GHz
[codecarbon WARNING @ 00:58:32] No CPU tracking mode found. Falling back on CPU constant mode.
[codecarbon INFO @ 00:58:32] [setup] GPU Tracking...
[codecarbon INFO @ 00:58:32] No GPU found.
[codecarbon INFO @ 00:58:32] The below tracking methods have been set up:
                RAM Tracking Method: RAM power estimation model
                CPU Tracking Method: global constant
                GPU Tracking Method: Unspecified
            
[codecarbon INFO @ 00:58:32] >>> Tracker's metadata:
[codecarbon INFO @ 00:58:32]   Platf

Saved model to /content/nodes/node_3_baseline.pkl

Training baseline for: /content/nodes/node_4.csv


[codecarbon WARNING @ 00:58:56] We saw that you have a Intel(R) Xeon(R) CPU @ 2.20GHz but we don't know it. Please contact us.
[codecarbon WARNING @ 00:58:56] No CPU tracking mode found. Falling back on estimation based on TDP for CPU. 
 Linux OS detected: Please ensure RAPL files exist, and are readable, at /sys/class/powercap/intel-rapl/subsystem to measure CPU

[codecarbon INFO @ 00:58:56] CPU Model on constant consumption mode: Intel(R) Xeon(R) CPU @ 2.20GHz
[codecarbon WARNING @ 00:58:56] No CPU tracking mode found. Falling back on CPU constant mode.
[codecarbon INFO @ 00:58:56] [setup] GPU Tracking...
[codecarbon INFO @ 00:58:56] No GPU found.
[codecarbon INFO @ 00:58:56] The below tracking methods have been set up:
                RAM Tracking Method: RAM power estimation model
                CPU Tracking Method: global constant
                GPU Tracking Method: Unspecified
            
[codecarbon INFO @ 00:58:56] >>> Tracker's metadata:
[codecarbon INFO @ 00:58:56]   Platf

Saved model to /content/nodes/node_4_baseline.pkl

=== BASELINE ENERGY + METRICS FOR ALL NODES ===
                        node      rmse       mae       smape    co2_kg  \
0  /content/nodes/node_1.csv  0.008886  0.005196  116.210919  0.000137   
1  /content/nodes/node_2.csv  0.010360  0.007420  112.159280  0.000085   
2  /content/nodes/node_3.csv  0.009273  0.006539  124.864069  0.000086   
3  /content/nodes/node_4.csv  0.009921  0.006486  112.713069  0.000081   

   energy_kwh  cpu_energy_kwh  ram_energy_kwh  
0    0.000513        0.000416        0.000097  
1    0.000318        0.000258        0.000060  
2    0.000322        0.000261        0.000061  
3    0.000302        0.000244        0.000057  


In [12]:
from codecarbon import EmissionsTracker
import numpy as np
import pandas as pd
import glob
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, mean_absolute_error


def smape(true, pred):
    denom = (np.abs(true) + np.abs(pred)) / 2
    return np.mean(np.abs(true - pred) / (denom + 1e-6)) * 100


# -----------------------------
# Load all node CSVs and merge
# -----------------------------
node_files = sorted(glob.glob("/content/nodes/node_*.csv"))
dfs = []

for n in node_files:
    df = pd.read_csv(n)
    df = df.dropna(subset=["cpu_avg"])

    df["cpu_hist_mean"] = df["cpu_hist_mean"].fillna(0)
    df["cpu_tail_mean"] = df["cpu_tail_mean"].fillna(0)

    dfs.append(df)

central = pd.concat(dfs, ignore_index=True)
central = central.dropna()

print("Centralized dataset shape:", central.shape)


FEATURES = [
    "cpu_avg", "cpu_max",
    "req_cpu", "req_mem",
    "mem_avg", "mem_max",
    "assigned_memory",
    "page_cache_memory",
    "cycles_per_instruction",
    "memory_accesses_per_instruction",
    "cpu_hist_mean",
    "cpu_tail_mean",
]

TARGET = "cpu_avg"
central = central.sort_values("time")

X = central[FEATURES].values
y = central[TARGET].shift(-1).values


# -----------------------------
# Safety checks
# -----------------------------
if len(X) == 0 or len(y) == 0:
    print("X or y empty after shift. STOP.")
else:
    central = central.iloc[:-1]
    X = X[:-1]
    y = y[:-1]

    if len(X) == 0 or len(y) == 0:
        print("Warning: No usable rows for training after final slice. Skipping.")
    else:
        X_train, X_test, y_train, y_test = train_test_split(
            X, y, test_size=0.2, shuffle=False
        )


        # Start of energy Tracking

        tracker = EmissionsTracker(project_name="centralized_baseline", measure_power_secs=1)
        tracker.start()


        # Train mode
        model = RandomForestRegressor(
            n_estimators=200,
            max_depth=14,
            n_jobs=-1,
            random_state=42
        )

        model.fit(X_train, y_train)
        preds = model.predict(X_test)


        #Energy Tracking stop

        co2_kg = tracker.stop()

        # Extract total energy + CPU + RAM
        final_data = tracker.final_emissions_data
        total_energy_kwh = final_data.energy_consumed if final_data else 0
        cpu_energy_kwh = final_data.cpu_energy if final_data else 0
        ram_energy_kwh = final_data.ram_energy if final_data else 0

        # Metrics
        rmse = np.sqrt(mean_squared_error(y_test, preds))
        mae = mean_absolute_error(y_test, preds)
        smape_val = smape(y_test, preds)

        print("\n=== CENTRALIZED BASELINE RESULTS ===")
        print("RMSE :", rmse)
        print("MAE  :", mae)
        print("SMAPE:", smape_val)
        print("CO₂ Emissions (kg):", co2_kg)
        print("Total Energy (kWh):", total_energy_kwh)
        print("CPU Energy (kWh):", cpu_energy_kwh)
        print("RAM Energy (kWh):", ram_energy_kwh)

Centralized dataset shape: (281185, 22)


[codecarbon WARNING @ 00:59:27] Multiple instances of codecarbon are allowed to run at the same time.
[codecarbon INFO @ 00:59:27] [setup] RAM Tracking...
[codecarbon INFO @ 00:59:27] [setup] CPU Tracking...
[codecarbon WARNING @ 00:59:29] We saw that you have a Intel(R) Xeon(R) CPU @ 2.20GHz but we don't know it. Please contact us.
[codecarbon WARNING @ 00:59:29] No CPU tracking mode found. Falling back on estimation based on TDP for CPU. 
 Linux OS detected: Please ensure RAPL files exist, and are readable, at /sys/class/powercap/intel-rapl/subsystem to measure CPU

[codecarbon INFO @ 00:59:29] CPU Model on constant consumption mode: Intel(R) Xeon(R) CPU @ 2.20GHz
[codecarbon WARNING @ 00:59:29] No CPU tracking mode found. Falling back on CPU constant mode.
[codecarbon INFO @ 00:59:29] [setup] GPU Tracking...
[codecarbon INFO @ 00:59:29] No GPU found.
[codecarbon INFO @ 00:59:29] The below tracking methods have been set up:
                RAM Tracking Method: RAM power estimation mo


=== CENTRALIZED BASELINE RESULTS ===
RMSE : 0.009734338633951501
MAE  : 0.006706546254303034
SMAPE: 121.11615363759485
CO₂ Emissions (kg): 0.0005364674902189605
Total Energy (kWh): 0.0020045717101694195
CPU Energy (kWh): 0.0016242165187388706
RAM Energy (kWh): 0.0003803551914305494


In [13]:
import pandas as pd

# ============================
# 1. BASELINE RESULTS (REBUILT)
# ============================

baseline_results_df = pd.DataFrame([
    {
        "node": "/content/nodes/node_1.csv",
        "rmse": 0.008886,
        "mae": 0.005196,
        "smape": 116.210919,
        "co2_kg": 0.000136,
    },
    {
        "node": "/content/nodes/node_2.csv",
        "rmse": 0.010360,
        "mae": 0.007420,
        "smape": 112.159280,
        "co2_kg": 0.000090,
    },
    {
        "node": "/content/nodes/node_3.csv",
        "rmse": 0.009273,
        "mae": 0.006539,
        "smape": 124.864069,
        "co2_kg": 0.000094,
    },
    {
        "node": "/content/nodes/node_4.csv",
        "rmse": 0.009921,
        "mae": 0.006486,
        "smape": 112.713069,
        "co2_kg": 0.000082,
    },
])

print("Baseline results loaded:")
display(baseline_results_df)


# ============================================
# 2. CENTRALIZED MODEL METRICS (YOUR RESULTS)
# ============================================

central_rmse = 0.009734338633951501
central_mae = 0.006706546254303034
central_smape = 121.11615363759485
central_co2 = 0.0005062026000492753

print("\nCentralized metrics loaded:")
print("RMSE:", central_rmse)
print("MAE:", central_mae)
print("SMAPE:", central_smape)
print("CO2 (kg):", central_co2)


# ===========================================================
# 3. y_test and preds SHOULD ALREADY EXIST from your training
# ===========================================================

try:
    print("\nLength of y_test:", len(y_test))
    print("Length of preds :", len(preds))
except NameError:
    print("\n⚠️ WARNING: y_test and preds not found in memory.")
    print("Run the centralized model block again to recreate them.")


Baseline results loaded:


node      rmse       mae       smape    co2_kg
0  /content/nodes/node_1.csv  0.008886  0.005196  116.210919  0.000136
1  /content/nodes/node_2.csv  0.010360  0.007420  112.159280  0.000090
2  /content/nodes/node_3.csv  0.009273  0.006539  124.864069  0.000094
3  /content/nodes/node_4.csv  0.009921  0.006486  112.713069  0.000082


Centralized metrics loaded:
RMSE: 0.009734338633951501
MAE: 0.006706546254303034
SMAPE: 121.11615363759485
CO2 (kg): 0.0005062026000492753

Length of y_test: 56237
Length of preds : 56237


In [14]:
# Install Plotly (optional visualizations).

!pip install plotly

import plotly.graph_objects as go
import plotly.express as px
import pandas as pd
# 1) ENERGY CONSUMPTION BAR CHART

energy_df = baseline_results_df.copy()
energy_df["node"] = energy_df["node"].str.extract(r"(node_\d+)")

# Add for the centralized
central_row = pd.DataFrame({
    "node": ["centralized"],
    "co2_kg": [central_co2],
    "rmse": [central_rmse],
    "mae": [central_mae],
    "smape": [central_smape]
})

energy_df = pd.concat([energy_df[["node","co2_kg"]], central_row[["node","co2_kg"]]])

fig1 = px.bar(
    energy_df,
    x="node",
    y="co2_kg",
    title="Energy Consumption (kg CO₂) — Baseline Nodes vs Centralized",
    labels={"node": "Node", "co2_kg": "CO₂ Emissions (kg)"},
    color="node",
    text="co2_kg"
)
fig1.update_traces(texttemplate='%{text:.6f}', textposition='outside')
fig1.update_layout(yaxis=dict(title="CO₂ Emissions (kg)", tickformat=".6f"))
fig1.show()

# 2) RMSE COMPARISON BAR CHART
rmse_df = baseline_results_df.copy()
rmse_df["node"] = rmse_df["node"].str.extract(r"(node_\d+)")

rmse_df = pd.concat([rmse_df[["node","rmse"]], central_row[["node","rmse"]]])

fig2 = px.bar(
    rmse_df,
    x="node",
    y="rmse",
    title="RMSE Comparison — Nodes vs Centralized",
    labels={"node": "Node", "rmse": "RMSE"},
    color="node",
    text="rmse"
)
fig2.update_traces(texttemplate='%{text:.5f}', textposition='outside')
fig2.update_layout(yaxis=dict(title="RMSE", tickformat=".5f"))
fig2.show()

# 3) PREDICTED VS ACTUAL (CENTRALIZED)
scatter_df = pd.DataFrame({
    "Actual": y_test,
    "Predicted": preds
})

fig3 = go.Figure()

fig3.add_trace(go.Scatter(
    x=scatter_df["Actual"],
    y=scatter_df["Predicted"],
    mode="markers",
    name="Predictions",
    opacity=0.5
))

# Line of perfect prediction
fig3.add_trace(go.Scatter(
    x=scatter_df["Actual"],
    y=scatter_df["Actual"],
    mode="lines",
    name="Perfect Prediction",
    line=dict(color="red", dash="dash")
))

fig3.update_layout(
    title="Predicted vs Actual CPU Usage (Centralized Model)",
    xaxis_title="Actual CPU Usage",
    yaxis_title="Predicted CPU Usage",
    width=700,
    height=600
)

fig3.show()


In [15]:
import pandas as pd
import os

NODE_DIR = "/content/nodes"
NODE_FILES = [f"{NODE_DIR}/node_{i}.csv" for i in range(1, 5)]

for path in NODE_FILES:
    print("\nChecking:", path)
    if os.path.exists(path):
        df = pd.read_csv(path)
        print("Rows:", df.shape[0], "Columns:", df.shape[1])
    else:
        print("❌ Missing file:", path)



Checking: /content/nodes/node_1.csv
Rows: 95719 Columns: 22

Checking: /content/nodes/node_2.csv
Rows: 104015 Columns: 22

Checking: /content/nodes/node_3.csv
Rows: 104316 Columns: 22

Checking: /content/nodes/node_4.csv
Rows: 101844 Columns: 22


## 5) Node-level data preparation (per client)
Each node loads its slice of data, fills missing values, and creates the next-step target (`y_next`).

In [16]:
# Utility: quick test of node cleaning + feature/target creation.

def test_prepare_node(node_path):
    df = pd.read_csv(node_path)

    print("Before cleaning:", df.shape)

    df = df.dropna(subset=["cpu_avg", "cpu_max"])

    df["time"] = pd.to_datetime(df["time"], errors="coerce")
    df = df.sort_values("time")

    df["cpu_hist_mean"] = df["cpu_hist_mean"].fillna(0)
    df["cpu_tail_mean"] = df["cpu_tail_mean"].fillna(0)

    FEATURES = [
        "cpu_avg", "cpu_max",
        "req_cpu", "req_mem",
        "mem_avg", "mem_max",
        "assigned_memory",
        "page_cache_memory",
        "cycles_per_instruction",
        "memory_accesses_per_instruction",
        "cpu_hist_mean",
        "cpu_tail_mean",
    ]

    df = df.dropna(subset=FEATURES)

    df["y_next"] = df["cpu_avg"].shift(-1)
    df = df.iloc[:-1]

    print("After cleaning:", df.shape)

    print(df.head())


In [17]:
# Run the node-prep test on a sample node file.

test_prepare_node("/content/nodes/node_1.csv")


Before cleaning: (95719, 22)
After cleaning: (65574, 23)
            time  machine_id  scheduling_class  priority  \
35409 1970-01-01   219242261                 3       200   
77934 1970-01-01   140392302                 0       103   
30121 1970-01-01  2311487507                 2       205   
77932 1970-01-01   155285925                 3       103   
77928 1970-01-01    21307911                 1       105   

                                        resource_request  \
35409  {'cpus': 0.04400634765625, 'memory': 0.0050659...   
77934  {'cpus': 0.0211181640625, 'memory': 0.01657104...   
30121  {'cpus': 0.002025604248046875, 'memory': 0.002...   
77932  {'cpus': 0.002025604248046875, 'memory': 0.001...   
77928  {'cpus': 0.0066070556640625, 'memory': 0.00521...   

                                           average_usage  \
35409  {'cpus': 0.004486083984375, 'memory': 0.002483...   
77934  {'cpus': 0.0001239776611328125, 'memory': 0.00...   
30121  {'cpus': 0.0004634857177734375, 'm

## 6) Model + training utilities
Define the PyTorch model, dataset/dataloader, local training loop, and FedAvg aggregation helpers.

In [18]:
import torch.nn as nn
import torch

class CPUForecastNet(nn.Module):
    def __init__(self, input_dim):
        super().__init__()
        self.net = nn.Sequential(
            nn.Linear(input_dim, 64),
            nn.ReLU(),
            nn.Linear(64, 32),
            nn.ReLU(),
            nn.Linear(32, 1)
        )

    def forward(self, x):
        return self.net(x)

# test run
model = CPUForecastNet(12)
test_input = torch.randn(1, 12)
print(model(test_input))


tensor([[0.1206]], grad_fn=<AddmmBackward0>)


In [19]:
# Function: prepare node data (features + next-step target).

def prepare_node_data(path):

    print(f"\nLoading node file: {path}")
    df = pd.read_csv(path)
    print("Raw shape:", df.shape)

    # Drop unusable rows
    df = df.dropna(subset=["cpu_avg", "cpu_max"])

    df["time"] = pd.to_datetime(df["time"], errors="coerce")
    df = df.sort_values("time")

    # Histograms often NaN → fill with 0
    df["cpu_hist_mean"] = df["cpu_hist_mean"].fillna(0)
    df["cpu_tail_mean"] = df["cpu_tail_mean"].fillna(0)

    FEATURES = [
        "cpu_avg", "cpu_max",
        "req_cpu", "req_mem",
        "mem_avg", "mem_max",
        "assigned_memory",
        "page_cache_memory",
        "cycles_per_instruction",
        "memory_accesses_per_instruction",
        "cpu_hist_mean",
        "cpu_tail_mean",
    ]

    df = df.dropna(subset=FEATURES)

    # Next-step prediction label
    df["y_next"] = df["cpu_avg"].shift(-1)
    df = df.iloc[:-1]

    X = df[FEATURES].values.astype(np.float32)
    y = df["y_next"].values.astype(np.float32)

    print("Clean shape:", X.shape, y.shape)

    return X, y


In [20]:
from torch.utils.data import Dataset, DataLoader
import torch

class NodeDataset(Dataset):
    def __init__(self, X, y):
        self.X = torch.tensor(X, dtype=torch.float32)
        self.y = torch.tensor(y, dtype=torch.float32).view(-1, 1)

    def __len__(self):
        return len(self.X)

    def __getitem__(self, idx):
        return self.X[idx], self.y[idx]

# Load Node 1
X1, y1 = prepare_node_data("/content/nodes/node_1.csv")

ds1 = NodeDataset(X1, y1)
loader1 = DataLoader(ds1, batch_size=256, shuffle=True)

model = CPUForecastNet(len(FEATURES))
optimizer = torch.optim.Adam(model.parameters(), lr=1e-3)
loss_fn = nn.MSELoss()

# perform ONE training step
for batch in loader1:
    Xb, yb = batch
    preds = model(Xb)
    loss = loss_fn(preds, yb)
    loss.backward()
    optimizer.step()
    break

print("Local training step successful! Loss =", loss.item())



Loading node file: /content/nodes/node_1.csv
Raw shape: (95719, 22)
Clean shape: (65574, 12) (65574,)
Local training step successful! Loss = 0.020095407962799072


In [21]:
from torch.utils.data import Dataset, DataLoader
import torch
import torch.nn as nn
import numpy as np

# ================
# 1. Wrap datasets
# ================
class NodeDataset(Dataset):
    def __init__(self, X, y):
        self.X = torch.tensor(X, dtype=torch.float32)
        self.y = torch.tensor(y, dtype=torch.float32).view(-1, 1)

    def __len__(self):
        return len(self.X)

    def __getitem__(self, idx):
        return self.X[idx], self.y[idx]

node_datasets = []
node_sizes = []

NODE_FILES = [
    "/content/nodes/node_1.csv",
    "/content/nodes/node_2.csv",
    "/content/nodes/node_3.csv",
    "/content/nodes/node_4.csv"
]

for path in NODE_FILES:
    Xn, yn = prepare_node_data(path)
    ds = NodeDataset(Xn, yn)
    node_datasets.append(ds)
    node_sizes.append(len(ds))

print("Loaded", len(node_datasets), "nodes")
print("Node sizes:", node_sizes)

# =================
# 2. Build model
# =================
class CPUForecastNet(nn.Module):
    def __init__(self, input_dim):
        super().__init__()
        self.net = nn.Sequential(
            nn.Linear(input_dim, 64),
            nn.ReLU(),
            nn.Linear(64, 32),
            nn.ReLU(),
            nn.Linear(32, 1)
        )
    def forward(self, x):
        return self.net(x)

def get_model():
    return CPUForecastNet(12)

DEVICE = "cuda" if torch.cuda.is_available() else "cpu"
print("Using device:", DEVICE)

# ==============================
# 3. Local training on each node
# ==============================
def train_local(model, dataloader, epochs=2, lr=1e-3):
    model.train()
    optim = torch.optim.Adam(model.parameters(), lr=lr)
    loss_fn = nn.MSELoss()

    for _ in range(epochs):
        for Xb, yb in dataloader:
            Xb, yb = Xb.to(DEVICE), yb.to(DEVICE)
            optim.zero_grad()
            preds = model(Xb)
            loss = loss_fn(preds, yb)
            loss.backward()
            optim.step()

    return model

# ==============================
# 4. Federated Averaging helpers
# ==============================
def get_state_dict(model):
    return {k: v.cpu().clone() for k, v in model.state_dict().items()}

def set_state_dict(model, state_dict):
    model.load_state_dict(state_dict)

def fedavg(states, weights):
    new_state = {}
    for key in states[0].keys():
        new_state[key] = sum(w * s[key] for s, w in zip(states, weights))
    return new_state

# ==============================
# 5. Train FL Global Model
# ==============================
global_model = get_model().to(DEVICE)

ROUNDS = 5
LOCAL_EPOCHS = 2

for rnd in range(1, ROUNDS + 1):
    print(f"\n===================")
    print(f"   FL ROUND {rnd}")
    print(f"===================")

    state_dicts = []
    sample_counts = []

    for i, ds in enumerate(node_datasets):
        print(f"\n--- Client {i+1} training on {len(ds)} samples ---")

        loader = DataLoader(ds, batch_size=256, shuffle=True)

        # copy global → local
        local_model = get_model().to(DEVICE)
        set_state_dict(local_model, get_state_dict(global_model))

        # train locally
        local_model = train_local(local_model, loader, epochs=LOCAL_EPOCHS)

        # collect
        state_dicts.append(get_state_dict(local_model))
        sample_counts.append(len(ds))

    # Normalize weights
    total = sum(sample_counts)
    weights = [n / total for n in sample_counts]

    # FedAvg update
    new_state = fedavg(state_dicts, weights)
    set_state_dict(global_model, new_state)

print("\n🎉 Federated Learning Training Complete!")
torch.save(global_model.state_dict(), "/content/federated_global_model.pth")
print("Saved model → federated_global_model.pth")



Loading node file: /content/nodes/node_1.csv
Raw shape: (95719, 22)
Clean shape: (65574, 12) (65574,)

Loading node file: /content/nodes/node_2.csv
Raw shape: (104015, 22)
Clean shape: (76603, 12) (76603,)

Loading node file: /content/nodes/node_3.csv
Raw shape: (104316, 22)
Clean shape: (68899, 12) (68899,)

Loading node file: /content/nodes/node_4.csv
Raw shape: (101844, 22)
Clean shape: (70106, 12) (70106,)
Loaded 4 nodes
Node sizes: [65574, 76603, 68899, 70106]
Using device: cpu

   FL ROUND 1

--- Client 1 training on 65574 samples ---

--- Client 2 training on 76603 samples ---

--- Client 3 training on 68899 samples ---

--- Client 4 training on 70106 samples ---

   FL ROUND 2

--- Client 1 training on 65574 samples ---

--- Client 2 training on 76603 samples ---

--- Client 3 training on 68899 samples ---

--- Client 4 training on 70106 samples ---

   FL ROUND 3

--- Client 1 training on 65574 samples ---

--- Client 2 training on 76603 samples ---

--- Client 3 training on 

In [22]:
from codecarbon import EmissionsTracker

# ===============================
# START ENERGY / CO2 TRACKING
# ===============================
tracker = EmissionsTracker(
    project_name="federated_learning",
    measure_power_secs=1
)
tracker.start()

print("\n⚡ Energy tracking started for FL training...\n")

# ===============================================
# FEDERATED LEARNING TRAINING LOOP (WITH TRACKER)
# ===============================================
global_model = get_model().to(DEVICE)

ROUNDS = 5
LOCAL_EPOCHS = 2
LR = 1e-3

for rnd in range(1, ROUNDS + 1):
    print(f"\n===================")
    print(f"   FL ROUND {rnd}")
    print(f"===================")

    state_dicts = []
    sample_counts = []

    for i, ds in enumerate(node_datasets):
        print(f"\n--- Client {i+1} training on {len(ds)} samples ---")

        loader = DataLoader(ds, batch_size=256, shuffle=True)

        # Copy global → local
        local_model = get_model().to(DEVICE)
        set_state_dict(local_model, get_state_dict(global_model))

        # Local training
        local_model = train_local(local_model, loader, epochs=LOCAL_EPOCHS, lr=LR)

        # Collect weights for FedAvg
        state_dicts.append(get_state_dict(local_model))
        sample_counts.append(len(ds))

    # Normalize weights
    total = sum(sample_counts)
    weights = [n / total for n in sample_counts]

    # FedAvg
    new_state = fedavg(state_dicts, weights)
    set_state_dict(global_model, new_state)

# ===============================
# END ENERGY / CO2 TRACKING
# ===============================

co2_kg = tracker.stop()
final_data = tracker.final_emissions_data

total_energy_kwh = final_data.energy_consumed if final_data else 0
cpu_energy_kwh = final_data.cpu_energy if final_data else 0
ram_energy_kwh = final_data.ram_energy if final_data else 0

print("\n Federated Learning Training Complete!")
print("Saved model → federated_global_model.pth")

print("\n=== FL ENERGY & CO₂ RESULTS ===")
print("CO₂ Emissions (kg):", co2_kg)
print("Total Energy (kWh):", total_energy_kwh)
print("CPU Energy (kWh):", cpu_energy_kwh)
print("RAM Energy (kWh):", ram_energy_kwh)


[codecarbon WARNING @ 01:03:31] Multiple instances of codecarbon are allowed to run at the same time.
[codecarbon INFO @ 01:03:31] [setup] RAM Tracking...
[codecarbon INFO @ 01:03:31] [setup] CPU Tracking...
[codecarbon WARNING @ 01:03:33] We saw that you have a Intel(R) Xeon(R) CPU @ 2.20GHz but we don't know it. Please contact us.
[codecarbon WARNING @ 01:03:33] No CPU tracking mode found. Falling back on estimation based on TDP for CPU. 
 Linux OS detected: Please ensure RAPL files exist, and are readable, at /sys/class/powercap/intel-rapl/subsystem to measure CPU

[codecarbon INFO @ 01:03:33] CPU Model on constant consumption mode: Intel(R) Xeon(R) CPU @ 2.20GHz
[codecarbon WARNING @ 01:03:33] No CPU tracking mode found. Falling back on CPU constant mode.
[codecarbon INFO @ 01:03:33] [setup] GPU Tracking...
[codecarbon INFO @ 01:03:33] No GPU found.
[codecarbon INFO @ 01:03:33] The below tracking methods have been set up:
                RAM Tracking Method: RAM power estimation mo


⚡ Energy tracking started for FL training...


   FL ROUND 1

--- Client 1 training on 65574 samples ---


[codecarbon INFO @ 01:03:34] Energy consumed for RAM : 0.000003 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:03:34] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:03:34] Energy consumed for All CPU : 0.000012 kWh
[codecarbon INFO @ 01:03:34] 0.000015 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:03:35] Energy consumed for RAM : 0.000006 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:03:35] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:03:35] Energy consumed for All CPU : 0.000024 kWh
[codecarbon INFO @ 01:03:35] 0.000029 kWh of electricity and 0.000000 L of water were used since the beginning.



--- Client 2 training on 76603 samples ---


[codecarbon INFO @ 01:03:36] Energy consumed for RAM : 0.000008 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:03:36] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:03:36] Energy consumed for All CPU : 0.000035 kWh
[codecarbon INFO @ 01:03:36] 0.000044 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:03:37] Energy consumed for RAM : 0.000011 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:03:37] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:03:37] Energy consumed for All CPU : 0.000047 kWh
[codecarbon INFO @ 01:03:37] 0.000058 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:03:38] Energy consumed for RAM : 0.000014 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:03:38] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:03:38] Energy consumed for All CPU

...


--- Client 3 training on 68899 samples ---


[codecarbon INFO @ 01:04:20] Energy consumed for RAM : 0.000129 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:04:20] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:04:20] Energy consumed for All CPU : 0.000549 kWh
[codecarbon INFO @ 01:04:20] 0.000678 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:04:21] Energy consumed for RAM : 0.000131 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:04:21] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:04:21] Energy consumed for All CPU : 0.000561 kWh
[codecarbon INFO @ 01:04:21] 0.000692 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:04:21] 0.003862 g.CO2eq/s mean an estimation of 121.78268473090264 kg.CO2eq/year



--- Client 4 training on 70106 samples ---


[codecarbon INFO @ 01:04:22] Energy consumed for RAM : 0.000134 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:04:22] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:04:22] Energy consumed for All CPU : 0.000572 kWh
[codecarbon INFO @ 01:04:22] 0.000706 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:04:23] Energy consumed for RAM : 0.000137 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:04:23] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:04:23] Energy consumed for All CPU : 0.000584 kWh
[codecarbon INFO @ 01:04:23] 0.000721 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:04:24] Energy consumed for RAM : 0.000139 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:04:24] Delta energy consumed for CPU with constant : 0.000007 kWh, power : 42.5 W
[codecarbon INFO @ 01:04:24] Energy consumed for All CPU


 Federated Learning Training Complete!
Saved model → federated_global_model.pth

=== FL ENERGY & CO₂ RESULTS ===
CO₂ Emissions (kg): 0.00019523320607015023
Total Energy (kWh): 0.0007295110494284858
CPU Energy (kWh): 0.0005909219490145921
RAM Energy (kWh): 0.00013858910041389361


In [23]:
import torch
import numpy as np
from sklearn.metrics import mean_squared_error, mean_absolute_error

# Load your global model
global_model = get_model().to(DEVICE)
global_model.load_state_dict(torch.load("/content/federated_global_model.pth", map_location=DEVICE))
global_model.eval()

# Use the centralized dataset for evaluation
# (same one used for centralized model)
CENTRAL_FILE = "/content/clean_trace.csv"
df_central = pd.read_csv(CENTRAL_FILE)

# PREP SAME FEATURES AS CENTRALIZED MODEL
df_central["time"] = pd.to_datetime(df_central["time"])
df_central = df_central.sort_values("time")

# Fill histogram NaNs with 0
df_central["cpu_hist_mean"] = df_central["cpu_hist_mean"].fillna(0)
df_central["cpu_tail_mean"] = df_central["cpu_tail_mean"].fillna(0)

FEATURES = [
    "cpu_avg", "cpu_max",
    "req_cpu", "req_mem",
    "mem_avg", "mem_max",
    "assigned_memory",
    "page_cache_memory",
    "cycles_per_instruction",
    "memory_accesses_per_instruction",
    "cpu_hist_mean",
    "cpu_tail_mean",
]

df_central = df_central.dropna(subset=FEATURES)

# Next-step label
df_central["y_next"] = df_central["cpu_avg"].shift(-1)
df_central = df_central.iloc[:-1]

X = df_central[FEATURES].values.astype(np.float32)
y_true = df_central["y_next"].values.astype(np.float32)

# Convert to tensor
X_tensor = torch.tensor(X, dtype=torch.float32).to(DEVICE)

# Predict
with torch.no_grad():
    y_pred = global_model(X_tensor).cpu().numpy().flatten()

# Compute metrics
rmse_fl = np.sqrt(mean_squared_error(y_true, y_pred))
mae_fl = mean_absolute_error(y_true, y_pred)

def smape(y_true, y_pred):
    denominator = (np.abs(y_true) + np.abs(y_pred)) / 2
    diff = np.abs(y_true - y_pred) / (denominator + 1e-6)
    return np.mean(diff) * 100

smape_fl = smape(y_true, y_pred)

print("\n=== FEDERATED GLOBAL MODEL METRICS ===")
print("RMSE :", rmse_fl)
print("MAE  :", mae_fl)
print("SMAPE:", smape_fl)



=== FEDERATED GLOBAL MODEL METRICS ===
RMSE : 0.011533054434425876
MAE  : 0.006354958284646273
SMAPE: 115.35282


In [24]:
import pandas as pd

# UK cost assumptions (references in thesis)
UK_ELECTRICITY_COST_PER_KWH = 0.30   # DESNZ, 2024
UK_CARBON_PRICE_PER_KG = 0.05        # UK ETS equivalent (£50/ton)

def compute_costs(df):
    df["energy_cost_£"] = df["energy_kwh"] * UK_ELECTRICITY_COST_PER_KWH
    df["carbon_cost_£"] = df["co2_kg"] * UK_CARBON_PRICE_PER_KG
    df["total_cost_£"] = df["energy_cost_£"] + df["carbon_cost_£"]
    return df

# Local nodes DataFrame
local_df = pd.DataFrame({
    "node": ["node1", "node2", "node3", "node4"],
    "rmse": [0.008886, 0.010360, 0.009273, 0.009921],
    "mae": [0.005196, 0.007420, 0.006539, 0.006486],
    "smape": [116.21, 112.16, 124.86, 112.71],
    "co2_kg": [0.000077, 0.000054, 0.000052, 0.000043],
    "energy_kwh": [0.000553, 0.000392, 0.000371, 0.000313]
})

local_df = compute_costs(local_df)


# Centralized model
centralized = {
    "co2_kg": 0.0002460463,
    "energy_kwh": 0.00177330895
}

centralized_df = pd.DataFrame([centralized])
centralized_df = compute_costs(centralized_df)


# Federated model
fl = {
    "co2_kg": 0.0001064587,
    "energy_kwh": 0.0007672710
}

fl_df = pd.DataFrame([fl])
fl_df = compute_costs(fl_df)

print("\n=== LOCAL COSTS (UK £) ===")
print(local_df[["node","energy_cost_£","carbon_cost_£","total_cost_£"]])

print("\n=== CENTRALIZED COST ===")
print(centralized_df[["energy_cost_£","carbon_cost_£","total_cost_£"]])

print("\n=== FEDERATED COST ===")
print(fl_df[["energy_cost_£","carbon_cost_£","total_cost_£"]])



=== LOCAL COSTS (UK £) ===
    node  energy_cost_£  carbon_cost_£  total_cost_£
0  node1       0.000166       0.000004      0.000170
1  node2       0.000118       0.000003      0.000120
2  node3       0.000111       0.000003      0.000114
3  node4       0.000094       0.000002      0.000096

=== CENTRALIZED COST ===
   energy_cost_£  carbon_cost_£  total_cost_£
0       0.000532       0.000012      0.000544

=== FEDERATED COST ===
   energy_cost_£  carbon_cost_£  total_cost_£
0        0.00023       0.000005      0.000236


In [25]:
import pandas as pd
import numpy as np

def prepare_node_data(path):

    print(f"\nLoading node file: {path}")
    df = pd.read_csv(path)
    print("Raw shape:", df.shape)

    # Drop unusable rows
    df = df.dropna(subset=["cpu_avg", "cpu_max"])

    df["time"] = pd.to_datetime(df["time"], errors="coerce")
    df = df.sort_values("time")

    # Histograms often NaN → fill with 0
    df["cpu_hist_mean"] = df["cpu_hist_mean"].fillna(0)
    df["cpu_tail_mean"] = df["cpu_tail_mean"].fillna(0)

    FEATURES = [
        "cpu_avg", "cpu_max",
        "req_cpu", "req_mem",
        "mem_avg", "mem_max",
        "assigned_memory",
        "page_cache_memory",
        "cycles_per_instruction",
        "memory_accesses_per_instruction",
        "cpu_hist_mean",
        "cpu_tail_mean",
    ]

    df = df.dropna(subset=FEATURES)

    # Next-step prediction label
    df["y_next"] = df["cpu_avg"].shift(-1)
    df = df.iloc[:-1]

    X = df[FEATURES].values.astype(np.float32)
    y = df["y_next"].values.astype(np.float32)

    print("Clean shape:", X.shape, y.shape)

    return X, y


## 7) Federated Learning runner
Runs FL for a chosen number of rounds/nodes, tracks energy with CodeCarbon, and evaluates on a centralized dataset.

In [26]:
# Core FL routine: FedAvg training, CodeCarbon tracking, and evaluation metrics (RMSE/MAE/SMAPE).

from codecarbon import EmissionsTracker
import torch
import numpy as np
from sklearn.metrics import mean_squared_error, mean_absolute_error

def evaluate_global_model(global_model, df):
    """Evaluate trained global FL model on centralized dataset."""

    df["time"] = pd.to_datetime(df["time"])
    df = df.sort_values("time")

    # Fill histogram NaNs
    df["cpu_hist_mean"] = df["cpu_hist_mean"].fillna(0)
    df["cpu_tail_mean"] = df["cpu_tail_mean"].fillna(0)

    FEATURES = [
        "cpu_avg", "cpu_max",
        "req_cpu", "req_mem",
        "mem_avg", "mem_max",
        "assigned_memory",
        "page_cache_memory",
        "cycles_per_instruction",
        "memory_accesses_per_instruction",
        "cpu_hist_mean",
        "cpu_tail_mean",
    ]

    df = df.dropna(subset=FEATURES)

    df["y_next"] = df["cpu_avg"].shift(-1)
    df = df.iloc[:-1]

    X = df[FEATURES].values.astype(np.float32)
    y_true = df["y_next"].values.astype(np.float32)

    X_tensor = torch.tensor(X, dtype=torch.float32).to(DEVICE)

    with torch.no_grad():
        y_pred = global_model(X_tensor).cpu().numpy().flatten()

    rmse = np.sqrt(mean_squared_error(y_true, y_pred))
    mae = mean_absolute_error(y_true, y_pred)

    def smape(y_true, y_pred):
        denominator = (np.abs(y_true) + np.abs(y_pred)) / 2
        diff = np.abs(y_true - y_pred) / (denominator + 1e-6)
        return np.mean(diff) * 100

    return rmse, mae, smape(y_true, y_pred)



def run_federated_learning(node_paths, rounds=5, local_epochs=2, lr=1e-3):
    """Run FL + carbon tracking + evaluation."""
    global global_model

    # Prepare datasets
    node_datasets = []
    sample_counts = []

    for path in node_paths:
        Xn, yn = prepare_node_data(path)
        ds = NodeDataset(Xn, yn)
        node_datasets.append(ds)
        sample_counts.append(len(ds))

    # Init global model
    global_model = get_model().to(DEVICE)

    # Track energy
    tracker = EmissionsTracker(
        project_name=f"FL_{len(node_paths)}nodes_{rounds}rounds",
        measure_power_secs=1
    )
    tracker.start()

    # FL rounds
    for rnd in range(1, rounds + 1):
        print(f"\n====== ROUND {rnd}/{rounds} ======")

        state_dicts = []
        for i, ds in enumerate(node_datasets):
            loader = DataLoader(ds, batch_size=256, shuffle=True)

            local_model = get_model().to(DEVICE)
            set_state_dict(local_model, get_state_dict(global_model))

            local_model = train_local(local_model, loader, epochs=local_epochs, lr=lr)

            state_dicts.append(get_state_dict(local_model))

        total = sum(sample_counts)
        weights = [n / total for n in sample_counts]

        new_state = fedavg(state_dicts, weights)
        set_state_dict(global_model, new_state)

    # Stop energy tracker
    co2 = tracker.stop()
    final_data = tracker.final_emissions_data

    energy_kwh = final_data.energy_consumed
    cpu_energy = final_data.cpu_energy
    ram_energy = final_data.ram_energy

    # Evaluate model on centralized dataset
    df_central = pd.read_csv("/content/clean_trace.csv")
    rmse, mae, smape_val = evaluate_global_model(global_model, df_central)

    return {
        "rmse": rmse,
        "mae": mae,
        "smape": smape_val,
        "co2_kg": co2,
        "energy_kwh": energy_kwh,
        "cpu_energy_kwh": cpu_energy,
        "ram_energy_kwh": ram_energy
    }


In [27]:
node_paths_4 = [
    "/content/nodes/node_1.csv",
    "/content/nodes/node_2.csv",
    "/content/nodes/node_3.csv",
    "/content/nodes/node_4.csv"
]

In [28]:
result_4nodes_5rounds = run_federated_learning(node_paths_4, rounds=5)


Loading node file: /content/nodes/node_1.csv
Raw shape: (95719, 22)
Clean shape: (65574, 12) (65574,)

Loading node file: /content/nodes/node_2.csv
Raw shape: (104015, 22)
Clean shape: (76603, 12) (76603,)

Loading node file: /content/nodes/node_3.csv
Raw shape: (104316, 22)
Clean shape: (68899, 12) (68899,)

Loading node file: /content/nodes/node_4.csv


[codecarbon WARNING @ 01:04:34] Multiple instances of codecarbon are allowed to run at the same time.
[codecarbon INFO @ 01:04:34] [setup] RAM Tracking...
[codecarbon INFO @ 01:04:34] [setup] CPU Tracking...


Raw shape: (101844, 22)
Clean shape: (70106, 12) (70106,)


[codecarbon WARNING @ 01:04:35] We saw that you have a Intel(R) Xeon(R) CPU @ 2.20GHz but we don't know it. Please contact us.
[codecarbon WARNING @ 01:04:35] No CPU tracking mode found. Falling back on estimation based on TDP for CPU. 
 Linux OS detected: Please ensure RAPL files exist, and are readable, at /sys/class/powercap/intel-rapl/subsystem to measure CPU

[codecarbon INFO @ 01:04:35] CPU Model on constant consumption mode: Intel(R) Xeon(R) CPU @ 2.20GHz
[codecarbon WARNING @ 01:04:35] No CPU tracking mode found. Falling back on CPU constant mode.
[codecarbon INFO @ 01:04:35] [setup] GPU Tracking...
[codecarbon INFO @ 01:04:35] No GPU found.
[codecarbon INFO @ 01:04:35] The below tracking methods have been set up:
                RAM Tracking Method: RAM power estimation model
                CPU Tracking Method: global constant
                GPU Tracking Method: Unspecified
            
[codecarbon INFO @ 01:04:35] >>> Tracker's metadata:
[codecarbon INFO @ 01:04:35]   Platf


====== ROUND 1/5 ======


...

[codecarbon INFO @ 01:04:56] Energy consumed for RAM : 0.000058 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:04:56] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:04:56] Energy consumed for All CPU : 0.000246 kWh
[codecarbon INFO @ 01:04:56] 0.000304 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:04:57] Energy consumed for RAM : 0.000060 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:04:57] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:04:57] Energy consumed for All CPU : 0.000258 kWh
[codecarbon INFO @ 01:04:57] 0.000318 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:04:58] Energy consumed for RAM : 0.000063 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:04:58] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:04:58] Energy consumed for All CPU


====== ROUND 4/5 ======


[codecarbon INFO @ 01:05:06] Energy consumed for RAM : 0.000085 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:05:06] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:05:06] Energy consumed for All CPU : 0.000363 kWh
[codecarbon INFO @ 01:05:06] 0.000448 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:05:07] Energy consumed for RAM : 0.000088 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:05:07] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:05:07] Energy consumed for All CPU : 0.000375 kWh
[codecarbon INFO @ 01:05:07] 0.000463 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:05:07] 0.003864 g.CO2eq/s mean an estimation of 121.84312950590028 kg.CO2eq/year
[codecarbon INFO @ 01:05:08] Energy consumed for RAM : 0.000091 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:05:08] Delta energy consumed for CP


====== ROUND 5/5 ======


[codecarbon INFO @ 01:05:16] Energy consumed for RAM : 0.000113 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:05:16] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:05:16] Energy consumed for All CPU : 0.000483 kWh
[codecarbon INFO @ 01:05:16] 0.000596 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:05:17] Energy consumed for RAM : 0.000116 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:05:17] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:05:17] Energy consumed for All CPU : 0.000495 kWh
[codecarbon INFO @ 01:05:17] 0.000611 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:05:18] Energy consumed for RAM : 0.000119 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:05:18] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:05:18] Energy consumed for All CPU

In [29]:
print("\n=== Federated Learning Run Results ===")
for key, value in result_4nodes_5rounds.items():
    if key != 'global_model': # global_model is a large object, don't print it directly
        print(f"{key.replace('_', ' ').capitalize()}: {value}")

# Optionally, save the global model if needed
# torch.save(result_4nodes_5rounds['global_model'].state_dict(), "/content/federated_global_model_final.pth")
# print("Saved final global model → federated_global_model_final.pth")


=== Federated Learning Run Results ===
Rmse: 0.011451026087230923
Mae: 0.0068835909478366375
Smape: 123.0834732055664
Co2 kg: 0.00019425412129402315
Energy kwh: 0.0007258525879562335
Cpu energy kwh: 0.0005879886253645686
Ram energy kwh: 0.00013786396259166496


In [30]:
print("\n=== Federated Learning Run Results ===")
for key, value in result_4nodes_5rounds.items():
    if key != 'global_model': # global_model is a large object, don't print it directly
        print(f"{key.replace('_', ' ').capitalize()}: {value}")

# Optionally, save the global model if needed
# torch.save(result_4nodes_5rounds['global_model'].state_dict(), "/content/federated_global_model_final.pth")
# print("Saved final global model → federated_global_model_final.pth")


=== Federated Learning Run Results ===
Rmse: 0.011451026087230923
Mae: 0.0068835909478366375
Smape: 123.0834732055664
Co2 kg: 0.00019425412129402315
Energy kwh: 0.0007258525879562335
Cpu energy kwh: 0.0005879886253645686
Ram energy kwh: 0.00013786396259166496


## 8) Create node splits
Split the cleaned dataset into multiple clients (4, 8, 12) and save each node CSV.

In [31]:
# Split the cleaned dataset into N nodes (clients) and write node CSVs.

def create_node_split(df, num_nodes, output_folder):
    import os
    import numpy as np

    os.makedirs(output_folder, exist_ok=True)

    machines = sorted(df["machine_id"].unique().tolist())
    machine_splits = np.array_split(machines, num_nodes)

    node_paths = []

    for i, group in enumerate(machine_splits, start=1):
        node_df = df[df["machine_id"].isin(group)].copy()
        path = f"{output_folder}/node_{i}.csv"
        node_df.to_csv(path, index=False)
        node_paths.append(path)

        print(f"Node {i}: {len(group)} machines → {node_df.shape[0]} rows")

    return node_paths


import pandas as pd
df_clean = pd.read_csv("/content/clean_trace.csv")

node_paths_4  = create_node_split(df_clean, 4,  "/content/nodes_4")
node_paths_8  = create_node_split(df_clean, 8,  "/content/nodes_8")
node_paths_12 = create_node_split(df_clean, 12, "/content/nodes_12")


Node 1: 24044 machines → 95719 rows
Node 2: 24044 machines → 104015 rows
Node 3: 24043 machines → 104316 rows
Node 4: 24043 machines → 101844 rows
Node 1: 12022 machines → 46394 rows
Node 2: 12022 machines → 49325 rows
Node 3: 12022 machines → 51128 rows
Node 4: 12022 machines → 52887 rows
Node 5: 12022 machines → 51592 rows
Node 6: 12022 machines → 52729 rows
Node 7: 12021 machines → 51363 rows
Node 8: 12021 machines → 50476 rows
Node 1: 8015 machines → 32227 rows
Node 2: 8015 machines → 30770 rows
Node 3: 8015 machines → 32726 rows
Node 4: 8015 machines → 33757 rows
Node 5: 8015 machines → 35320 rows
Node 6: 8015 machines → 34944 rows
Node 7: 8014 machines → 35053 rows
Node 8: 8014 machines → 33785 rows
Node 9: 8014 machines → 35473 rows
Node 10: 8014 machines → 34226 rows
Node 11: 8014 machines → 34789 rows
Node 12: 8014 machines → 32824 rows


In [32]:
import pandas as pd

all_results = []

def run_and_store(name, node_paths, rounds):
    print(f"\n\n====== RUNNING: {name} ======")
    result = run_federated_learning(node_paths, rounds=rounds)

    result["name"] = name
    result["num_nodes"] = len(node_paths)
    result["rounds"] = rounds

    all_results.append(result)
    return result


## 9) Run experiments + export results
Run multiple configurations and export a summary CSV of metrics + energy/CO₂.

In [33]:
# Run multiple experiment configurations and store results.

result_4_5  = run_and_store("4nodes_5rounds",  node_paths_4,  rounds=5)
result_4_10 = run_and_store("4nodes_10rounds", node_paths_4,  rounds=10)
result_4_20 = run_and_store("4nodes_20rounds", node_paths_4,  rounds=20)




====== RUNNING: 4nodes_5rounds ======

Loading node file: /content/nodes_4/node_1.csv
Raw shape: (95719, 22)
Clean shape: (65574, 12) (65574,)

Loading node file: /content/nodes_4/node_2.csv
Raw shape: (104015, 22)
Clean shape: (76603, 12) (76603,)

Loading node file: /content/nodes_4/node_3.csv
Raw shape: (104316, 22)
Clean shape: (68899, 12) (68899,)

Loading node file: /content/nodes_4/node_4.csv


[codecarbon WARNING @ 01:06:30] Multiple instances of codecarbon are allowed to run at the same time.
[codecarbon INFO @ 01:06:30] [setup] RAM Tracking...
[codecarbon INFO @ 01:06:30] [setup] CPU Tracking...


Raw shape: (101844, 22)
Clean shape: (70106, 12) (70106,)


[codecarbon WARNING @ 01:06:32] We saw that you have a Intel(R) Xeon(R) CPU @ 2.20GHz but we don't know it. Please contact us.
[codecarbon WARNING @ 01:06:32] No CPU tracking mode found. Falling back on estimation based on TDP for CPU. 
 Linux OS detected: Please ensure RAPL files exist, and are readable, at /sys/class/powercap/intel-rapl/subsystem to measure CPU

[codecarbon INFO @ 01:06:32] CPU Model on constant consumption mode: Intel(R) Xeon(R) CPU @ 2.20GHz
[codecarbon WARNING @ 01:06:32] No CPU tracking mode found. Falling back on CPU constant mode.
[codecarbon INFO @ 01:06:32] [setup] GPU Tracking...
[codecarbon INFO @ 01:06:32] No GPU found.
[codecarbon INFO @ 01:06:32] The below tracking methods have been set up:
                RAM Tracking Method: RAM power estimation model
                CPU Tracking Method: global constant
                GPU Tracking Method: Unspecified
            
[codecarbon INFO @ 01:06:32] >>> Tracker's metadata:
[codecarbon INFO @ 01:06:32]   Platf


====== ROUND 1/5 ======


...

[codecarbon INFO @ 01:12:15] Energy consumed for RAM : 0.000484 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:12:15] Delta energy consumed for CPU with constant : 0.000014 kWh, power : 42.5 W
[codecarbon INFO @ 01:12:15] Energy consumed for All CPU : 0.002065 kWh
[codecarbon INFO @ 01:12:15] 0.002549 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:12:16] Energy consumed for RAM : 0.000487 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:12:16] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:12:16] Energy consumed for All CPU : 0.002076 kWh
[codecarbon INFO @ 01:12:16] 0.002563 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:12:16] 0.003834 g.CO2eq/s mean an estimation of 120.91846129693941 kg.CO2eq/year
[codecarbon INFO @ 01:12:17] Energy consumed for RAM : 0.000490 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:12:17] Delta energy consumed for CP


====== ROUND 19/20 ======


[codecarbon INFO @ 01:12:25] Energy consumed for RAM : 0.000512 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:12:25] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:12:25] Energy consumed for All CPU : 0.002185 kWh
[codecarbon INFO @ 01:12:25] 0.002698 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:12:26] Energy consumed for RAM : 0.000515 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:12:26] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:12:26] Energy consumed for All CPU : 0.002197 kWh
[codecarbon INFO @ 01:12:26] 0.002712 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:12:27] Energy consumed for RAM : 0.000518 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:12:27] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:12:27] Energy consumed for All CPU


====== ROUND 20/20 ======


[codecarbon INFO @ 01:12:35] Energy consumed for RAM : 0.000540 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:12:35] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:12:35] Energy consumed for All CPU : 0.002302 kWh
[codecarbon INFO @ 01:12:35] 0.002842 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:12:36] Energy consumed for RAM : 0.000542 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:12:36] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:12:36] Energy consumed for All CPU : 0.002314 kWh
[codecarbon INFO @ 01:12:36] 0.002856 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:12:37] Energy consumed for RAM : 0.000545 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:12:37] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:12:37] Energy consumed for All CPU

In [34]:
result_8_5  = run_and_store("8nodes_5rounds",  node_paths_8,  rounds=5)
result_8_10 = run_and_store("8nodes_10rounds", node_paths_8,  rounds=10)
result_8_20 = run_and_store("8nodes_20rounds", node_paths_8,  rounds=20)




====== RUNNING: 8nodes_5rounds ======

Loading node file: /content/nodes_8/node_1.csv
Raw shape: (46394, 22)
Clean shape: (31144, 12) (31144,)

Loading node file: /content/nodes_8/node_2.csv
Raw shape: (49325, 22)
Clean shape: (34429, 12) (34429,)

Loading node file: /content/nodes_8/node_3.csv
Raw shape: (51128, 22)
Clean shape: (37309, 12) (37309,)

Loading node file: /content/nodes_8/node_4.csv
Raw shape: (52887, 22)
Clean shape: (39293, 12) (39293,)

Loading node file: /content/nodes_8/node_5.csv
Raw shape: (51592, 22)
Clean shape: (34258, 12) (34258,)

Loading node file: /content/nodes_8/node_6.csv
Raw shape: (52729, 22)
Clean shape: (34643, 12) (34643,)

Loading node file: /content/nodes_8/node_7.csv
Raw shape: (51363, 22)
Clean shape: (36384, 12) (36384,)

Loading node file: /content/nodes_8/node_8.csv


[codecarbon WARNING @ 01:12:53] Multiple instances of codecarbon are allowed to run at the same time.
[codecarbon INFO @ 01:12:53] [setup] RAM Tracking...
[codecarbon INFO @ 01:12:53] [setup] CPU Tracking...


Raw shape: (50476, 22)
Clean shape: (33718, 12) (33718,)


[codecarbon WARNING @ 01:12:54] We saw that you have a Intel(R) Xeon(R) CPU @ 2.20GHz but we don't know it. Please contact us.
[codecarbon WARNING @ 01:12:54] No CPU tracking mode found. Falling back on estimation based on TDP for CPU. 
 Linux OS detected: Please ensure RAPL files exist, and are readable, at /sys/class/powercap/intel-rapl/subsystem to measure CPU

[codecarbon INFO @ 01:12:54] CPU Model on constant consumption mode: Intel(R) Xeon(R) CPU @ 2.20GHz
[codecarbon WARNING @ 01:12:54] No CPU tracking mode found. Falling back on CPU constant mode.
[codecarbon INFO @ 01:12:54] [setup] GPU Tracking...
[codecarbon INFO @ 01:12:54] No GPU found.
[codecarbon INFO @ 01:12:54] The below tracking methods have been set up:
                RAM Tracking Method: RAM power estimation model
                CPU Tracking Method: global constant
                GPU Tracking Method: Unspecified
            
[codecarbon INFO @ 01:12:54] >>> Tracker's metadata:
[codecarbon INFO @ 01:12:54]   Platf


====== ROUND 1/5 ======


...

[codecarbon INFO @ 01:18:29] Energy consumed for RAM : 0.000454 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:18:29] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:18:29] Energy consumed for All CPU : 0.001936 kWh
[codecarbon INFO @ 01:18:29] 0.002390 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:18:30] Energy consumed for RAM : 0.000457 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:18:30] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:18:30] Energy consumed for All CPU : 0.001947 kWh
[codecarbon INFO @ 01:18:30] 0.002404 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:18:31] Energy consumed for RAM : 0.000459 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:18:31] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:18:31] Energy consumed for All CPU


====== ROUND 19/20 ======


[codecarbon INFO @ 01:18:38] Energy consumed for RAM : 0.000479 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:18:38] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:18:38] Energy consumed for All CPU : 0.002041 kWh
[codecarbon INFO @ 01:18:38] 0.002520 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:18:39] Energy consumed for RAM : 0.000481 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:18:39] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:18:39] Energy consumed for All CPU : 0.002053 kWh
[codecarbon INFO @ 01:18:39] 0.002534 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:18:40] Energy consumed for RAM : 0.000484 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:18:40] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:18:40] Energy consumed for All CPU


====== ROUND 20/20 ======


[codecarbon INFO @ 01:18:48] Energy consumed for RAM : 0.000506 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:18:48] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:18:48] Energy consumed for All CPU : 0.002158 kWh
[codecarbon INFO @ 01:18:48] 0.002664 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:18:48] 0.003863 g.CO2eq/s mean an estimation of 121.80986856614835 kg.CO2eq/year
[codecarbon INFO @ 01:18:49] Energy consumed for RAM : 0.000509 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:18:49] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:18:49] Energy consumed for All CPU : 0.002170 kWh
[codecarbon INFO @ 01:18:49] 0.002678 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:18:50] Energy consumed for RAM : 0.000512 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:18:50] Delta energy consumed for CP

In [ ]:
result_12_5  = run_and_store("12nodes_5rounds",  node_paths_12, rounds=5)
result_12_10 = run_and_store("12nodes_10rounds", node_paths_12, rounds=10)
result_12_20 = run_and_store("12nodes_20rounds", node_paths_12, rounds=20)




====== RUNNING: 12nodes_5rounds ======

Loading node file: /content/nodes_12/node_1.csv
Raw shape: (32227, 22)
Clean shape: (20715, 12) (20715,)

Loading node file: /content/nodes_12/node_2.csv
Raw shape: (30770, 22)
Clean shape: (21750, 12) (21750,)

Loading node file: /content/nodes_12/node_3.csv
Raw shape: (32726, 22)
Clean shape: (23110, 12) (23110,)

Loading node file: /content/nodes_12/node_4.csv
Raw shape: (33757, 22)
Clean shape: (24474, 12) (24474,)

Loading node file: /content/nodes_12/node_5.csv
Raw shape: (35320, 22)
Clean shape: (27096, 12) (27096,)

Loading node file: /content/nodes_12/node_6.csv
Raw shape: (34944, 22)
Clean shape: (25035, 12) (25035,)

Loading node file: /content/nodes_12/node_7.csv
Raw shape: (35053, 22)
Clean shape: (22826, 12) (22826,)

Loading node file: /content/nodes_12/node_8.csv
Raw shape: (33785, 22)
Clean shape: (22894, 12) (22894,)

Loading node file: /content/nodes_12/node_9.csv
Raw shape: (35473, 22)
Clean shape: (23173, 12) (23173,)

Load

[codecarbon WARNING @ 01:19:05] Multiple instances of codecarbon are allowed to run at the same time.
[codecarbon INFO @ 01:19:05] [setup] RAM Tracking...
[codecarbon INFO @ 01:19:05] [setup] CPU Tracking...


Raw shape: (32824, 22)
Clean shape: (21482, 12) (21482,)


[codecarbon WARNING @ 01:19:06] We saw that you have a Intel(R) Xeon(R) CPU @ 2.20GHz but we don't know it. Please contact us.
[codecarbon WARNING @ 01:19:06] No CPU tracking mode found. Falling back on estimation based on TDP for CPU. 
 Linux OS detected: Please ensure RAPL files exist, and are readable, at /sys/class/powercap/intel-rapl/subsystem to measure CPU

[codecarbon INFO @ 01:19:06] CPU Model on constant consumption mode: Intel(R) Xeon(R) CPU @ 2.20GHz
[codecarbon WARNING @ 01:19:06] No CPU tracking mode found. Falling back on CPU constant mode.
[codecarbon INFO @ 01:19:06] [setup] GPU Tracking...
[codecarbon INFO @ 01:19:06] No GPU found.
[codecarbon INFO @ 01:19:06] The below tracking methods have been set up:
                RAM Tracking Method: RAM power estimation model
                CPU Tracking Method: global constant
                GPU Tracking Method: Unspecified
            
[codecarbon INFO @ 01:19:06] >>> Tracker's metadata:
[codecarbon INFO @ 01:19:06]   Platf


====== ROUND 1/5 ======


...

[codecarbon INFO @ 01:22:10] Energy consumed for RAM : 0.000053 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:22:10] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:22:10] Energy consumed for All CPU : 0.000224 kWh
[codecarbon INFO @ 01:22:10] 0.000277 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:22:11] Energy consumed for RAM : 0.000055 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:22:11] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:22:11] Energy consumed for All CPU : 0.000236 kWh
[codecarbon INFO @ 01:22:11] 0.000291 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:22:12] Energy consumed for RAM : 0.000059 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:22:12] Delta energy consumed for CPU with constant : 0.000015 kWh, power : 42.5 W
[codecarbon INFO @ 01:22:12] Energy consumed for All CPU


====== ROUND 4/20 ======


[codecarbon INFO @ 01:22:20] Energy consumed for RAM : 0.000081 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:22:20] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:22:20] Energy consumed for All CPU : 0.000344 kWh
[codecarbon INFO @ 01:22:20] 0.000425 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:22:21] Energy consumed for RAM : 0.000083 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:22:21] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:22:21] Energy consumed for All CPU : 0.000356 kWh
[codecarbon INFO @ 01:22:21] 0.000439 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:22:22] Energy consumed for RAM : 0.000086 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:22:22] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:22:22] Energy consumed for All CPU


====== ROUND 5/20 ======


[codecarbon INFO @ 01:22:30] Energy consumed for RAM : 0.000108 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:22:30] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:22:30] Energy consumed for All CPU : 0.000461 kWh
[codecarbon INFO @ 01:22:30] 0.000569 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:22:31] Energy consumed for RAM : 0.000111 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:22:31] Delta energy consumed for CPU with constant : 0.000012 kWh, power : 42.5 W
[codecarbon INFO @ 01:22:31] Energy consumed for All CPU : 0.000473 kWh
[codecarbon INFO @ 01:22:31] 0.000584 kWh of electricity and 0.000000 L of water were used since the beginning.
[codecarbon INFO @ 01:22:31] 0.003858 g.CO2eq/s mean an estimation of 121.65585497905889 kg.CO2eq/year
[codecarbon INFO @ 01:22:32] Energy consumed for RAM : 0.000114 kWh. RAM Power : 10.0 W
[codecarbon INFO @ 01:22:32] Delta energy consumed for CP

In [ ]:
# Export consolidated experiment results to CSV.

df_results = pd.DataFrame(all_results)
df_results.to_csv("/content/fl_experiments_results.csv", index=False)

df_results
